In [1]:
import h5py
import numpy as np
import sys
import tables
import pandas as pd
from astropy.io import fits
from ctapipe.io import EventSource
from ctapipe.io import TableLoader
from astropy.table import Table
from astropy.io import fits
from ctapipe.io import read_table
from ctapipe.utils.datasets import get_dataset_path
from ctapipe.visualization import CameraDisplay
from matplotlib import pyplot as plt
from ctapipe.io.hdf5eventsource import HDF5EventSource
from ctapipe.instrument import CameraGeometry

In [2]:
# See whats in the file
with fits.open("/home/leyre/Escritorio/cta-lstchain/LST_data/data/LST-1.4.Run02005.0000_first50.fits.fz") as hdul:
    hdul.info()
    print(hdul[2].columns)
   # want to see what's in event_id 
    print(hdul[2].data['event_id'])

Filename: /home/leyre/Escritorio/cta-lstchain/LST_data/data/LST-1.4.Run02005.0000_first50.fits.fz
No.    Name      Ver    Type      Cards   Dimensions   Format
  0  PRIMARY       1 PrimaryHDU       8   ()      
  1  CameraConfig    1 BinTableHDU    118   1R x 15C   [1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB]   
  2  Events        1 BinTableHDU    153   1R x 20C   [1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB, 1QB]   
ColDefs(
    name = 'configuration_id'; format = '1QB'; bzero = 9223372036854775807
    name = 'event_id'; format = '1QB'; bzero = 9223372036854775807
    name = 'tel_event_id'; format = '1QB'; bzero = 9223372036854775807
    name = 'trigger_time_s'; format = '1QB'; bzero = 2147483648
    name = 'trigger_time_qns'; format = '1QB'; bzero = 2147483648
    name = 'trigger_type'; format = '1QB'; bzero = 2147483648
    name = 'waveform'; format = '1QB'; bzero = 32678
    name = 'pixel_status'; form

In [3]:
fileName0 = "./dl1_LST-1.Run12162.0000.h5"
fileName1 = "./dl1_LST-1.Run12162.0001.h5"
fileName2 = "./dl1_LST-1.Run12162.0002.h5"
fileName3 = "./dl1_LST-1.Run12162.0003.h5"
#load dl2 with read_table
#tablee = read_table(fileName,"/dl2")
#dl2 = TableLoader(fileName, load_dl2=True)
#path = get_dataset_path(fileName)

# load dl1 with read_table
fileTable0 = tables.open_file(fileName0)
fileTable1 = tables.open_file(fileName1)
fileTable2 = tables.open_file(fileName2)
fileTable3 = tables.open_file(fileName3)


In [4]:
# Get images and parameters from dl1
images0 = fileTable0.root.dl1.event.telescope.image.LST_LSTCam
parameters0 = fileTable0.root.dl1.event.telescope.parameters.LST_LSTCam
images1 = fileTable1.root.dl1.event.telescope.image.LST_LSTCam
parameters1 = fileTable1.root.dl1.event.telescope.parameters.LST_LSTCam
images2 = fileTable2.root.dl1.event.telescope.image.LST_LSTCam
parameters2 = fileTable2.root.dl1.event.telescope.parameters.LST_LSTCam
images3 = fileTable3.root.dl1.event.telescope.image.LST_LSTCam
parameters3 = fileTable3.root.dl1.event.telescope.parameters.LST_LSTCam

In [5]:
file = h5py.File(fileName0, 'r')
print(list(file.keys()))

# do a depth 5 search of keys and se what we find
def print_attrs(name, obj):
    print(name)
    for key, val in obj.attrs.items():
        print("    %s: %s" % (key))
        #if val is a dict, recurse into it
        if isinstance(val, dict):
            print_attrs(name + "/" + key, val)

['configuration', 'dl1', 'source_filenames']


In [6]:
print(list(file.keys()))
# check if file is object with keys
if isinstance(file['dl1']['event'], h5py.Group):
    print('heyy')
else:
    print('nope')

# do a recursive search with depth 10 of all keys. 
def search_keys(obj, depth=0):
    # print(depth)
    # if depth > 10, stop
    if depth > 10:
        return
    for key in list(obj.keys()):

        for i in range(depth):
            print('\t', end='')
        print(depth, key)
        if isinstance(obj[key], h5py.Group):
            search_keys(obj[key], depth+1)
            
search_keys(file)
print(file['source_filenames']['filenames'])

['configuration', 'dl1', 'source_filenames']
heyy
0 configuration
	1 instrument
		2 subarray
			3 layout
			3 layout.__table_column_meta__
		2 telescope
			3 camera
				4 geometry_0
				4 geometry_0.__table_column_meta__
				4 readout_0
				4 readout_0.__table_column_meta__
			3 optics
			3 optics.__table_column_meta__
0 dl1
	1 event
		2 telescope
			3 image
				4 LST_LSTCam
			3 monitoring
				4 calibration
				4 flatfield
				4 pedestal
			3 parameters
				4 LST_LSTCam
0 source_filenames
	1 filenames
<HDF5 dataset "filenames": shape (1,), type "|S78">


In [7]:
dl1_group = file['source_filenames']
print(list(dl1_group.keys()))

['filenames']


In [8]:
#print size of images
print("Size of images: ", images0.shape)
siz = images0.shape[0]

Size of images:  (53000,)


In [9]:
cleaned0 = np.array(images0[0]['image'])
cleaned1 = np.array(images1[0]['image'])
cleaned2 = np.array(images2[0]['image'])
cleaned3 = np.array(images3[0]['image'])
print(len(cleaned0))

1855


In [10]:
# do the same for all images and save them in a new array
# first create the new array, with shape: len(cleaned) columns, siz rows
cleanImages0 = np.zeros((len(cleaned0), siz))
print(cleanImages0.shape)
# now fill with the array, applying the masks
counter = 0
for i in range(siz):
    image0 = np.array(images0[i]['image'])
    mask0 = np.array(images0[i]['image_mask'])
    # cleaned0 = image0.copy()
    # cleaned[~mask]=0
    cleanImages0[:,i] = cleaned0
    counter += 1
    if counter%100 == 0:
        print("Done: ", counter/siz * 100.0, "%")


(1855, 53000)
Done:  0.18867924528301888 %
Done:  0.37735849056603776 %
Done:  0.5660377358490566 %
Done:  0.7547169811320755 %
Done:  0.9433962264150944 %
Done:  1.1320754716981132 %
Done:  1.3207547169811322 %
Done:  1.509433962264151 %
Done:  1.6981132075471699 %
Done:  1.8867924528301887 %
Done:  2.0754716981132075 %
Done:  2.2641509433962264 %
Done:  2.4528301886792456 %
Done:  2.6415094339622645 %
Done:  2.8301886792452833 %
Done:  3.018867924528302 %
Done:  3.207547169811321 %
Done:  3.3962264150943398 %
Done:  3.5849056603773586 %
Done:  3.7735849056603774 %
Done:  3.9622641509433962 %
Done:  4.150943396226415 %
Done:  4.339622641509433 %


Done:  4.528301886792453 %
Done:  4.716981132075472 %
Done:  4.905660377358491 %
Done:  5.09433962264151 %
Done:  5.283018867924529 %
Done:  5.471698113207547 %
Done:  5.660377358490567 %
Done:  5.849056603773585 %
Done:  6.037735849056604 %
Done:  6.226415094339623 %
Done:  6.415094339622642 %
Done:  6.60377358490566 %
Done:  6.7924528301886795 %
Done:  6.981132075471698 %
Done:  7.169811320754717 %
Done:  7.3584905660377355 %
Done:  7.547169811320755 %
Done:  7.735849056603773 %
Done:  7.9245283018867925 %
Done:  8.11320754716981 %
Done:  8.30188679245283 %
Done:  8.49056603773585 %
Done:  8.679245283018867 %
Done:  8.867924528301886 %
Done:  9.056603773584905 %
Done:  9.245283018867925 %
Done:  9.433962264150944 %
Done:  9.622641509433963 %
Done:  9.811320754716983 %
Done:  10.0 %
Done:  10.18867924528302 %
Done:  10.377358490566039 %
Done:  10.566037735849058 %
Done:  10.754716981132075 %
Done:  10.943396226415095 %
Done:  11.132075471698114 %
Done:  11.320754716981133 %
Done:  11.

In [11]:
#save array in a new file / change name
np.save("cleanImages0.npy", cleanImages0)

In [12]:
cleanImages0 = np.load("cleanImages0.npy")
cleanImages1 = np.load("cleanImages1.npy")
cleanImages2 = np.load("cleanImages2.npy")
cleanImages3 = np.load("cleanImages3.npy")

In [13]:
cleanImages3.shape 

(1855, 53000)

Combine all the events in the same matrix

In [14]:
# Create an array that contains cleanImages0, cleanImages1, cleanImages2, cleanImages3 
# and has shape:  4 * siz columns and len(cleaned3) rows
cleanImages = np.zeros((len(cleaned3), 4*siz))
cleanImages.shape
# Fill it with the arrays
cleanImages[:, 0:siz] = cleanImages0
cleanImages[:, siz:2*siz] = cleanImages1
cleanImages[:, 2*siz:3*siz] = cleanImages2
cleanImages[:, 3*siz:4*siz] = cleanImages3

In [15]:
np.save("cleanImages.npy", cleanImages)

In [16]:
cleanImages.shape

(1855, 212000)

In [17]:
# Reduce the size of the images by a factor of 2 for 
reduction_factor = 2
counter = 0
reducedImages = np.zeros((int(len(cleanImages[:,0])/reduction_factor), len(cleanImages[0,:])))
print(reducedImages.shape)
# Loop over the events and make the mean of every reduction_factor pixels
for i in range(len(cleanImages[0,:])):
    print("Done: ", counter/len(cleanImages[0,:]) * 100.0, "%")
    counter += 1
    for j in range(len(cleanImages[:,0]) // reduction_factor):
            if j <= (len(cleanImages[:,0]) // reduction_factor) - 1:
                reducedImages[j, i] = np.mean((cleanImages[j * reduction_factor, i], cleanImages[(j * reduction_factor) + 1, i]))
            else:
                reducedImages[j, i] = cleanImages[j, i]


(927, 212000)
Done:  0.0 %
Done:  0.0004716981132075472 %
Done:  0.0009433962264150943 %
Done:  0.0014150943396226414 %
Done:  0.0018867924528301887 %
Done:  0.0023584905660377358 %
Done:  0.002830188679245283 %
Done:  0.0033018867924528303 %
Done:  0.0037735849056603774 %
Done:  0.0042452830188679245 %
Done:  0.0047169811320754715 %
Done:  0.005188679245283019 %
Done:  0.005660377358490566 %
Done:  0.006132075471698114 %
Done:  0.006603773584905661 %
Done:  0.007075471698113208 %
Done:  0.007547169811320755 %
Done:  0.008018867924528302 %
Done:  0.008490566037735849 %
Done:  0.008962264150943396 %
Done:  0.009433962264150943 %
Done:  0.00990566037735849 %
Done:  0.010377358490566037 %
Done:  0.010849056603773584 %
Done:  0.011320754716981131 %
Done:  0.01179245283018868 %
Done:  0.012264150943396227 %
Done:  0.012735849056603774 %
Done:  0.013207547169811321 %
Done:  0.013679245283018868 %
Done:  0.014150943396226415 %
Done:  0.014622641509433962 %
Done:  0.01509433962264151 %
Done:  

KeyboardInterrupt: 

In [ ]:
np.save("reducedImages.npy", reducedImages)

In [ ]:
reducedImages.shape

(927, 212000)

In [ ]:
cuttedImages = reducedImages.copy()
columns_to_delete = []  # Keep track of columns to delete
columns_to_maintain = []
for i in range(len(cuttedImages[0,:])):
    if np.max(cuttedImages[:,i]) < 5:
        columns_to_delete.append(i)
        print("Event to delete: ", i)
    else:
        columns_to_maintain.append(i)
print("Number of events to delete: ", len(columns_to_delete))

#new array with the columns to maintain
cuttedImages = np.zeros((len(reducedImages[:,0]), len(columns_to_maintain)))
#move all columns to be maintained using the list columns_to_maintain
cuttedImages = reducedImages[:,columns_to_maintain]
print("Number of events:", len(cuttedImages[0,:]))

Event to delete:  8
Event to delete:  24
Event to delete:  33
Event to delete:  35
Event to delete:  39
Event to delete:  69
Event to delete:  90
Event to delete:  96
Event to delete:  97
Event to delete:  106
Event to delete:  128
Event to delete:  161
Event to delete:  171
Event to delete:  177
Event to delete:  196
Event to delete:  198
Event to delete:  200
Event to delete:  205
Event to delete:  224
Event to delete:  227
Event to delete:  229
Event to delete:  231
Event to delete:  283
Event to delete:  290
Event to delete:  305
Event to delete:  309
Event to delete:  316
Event to delete:  320
Event to delete:  344
Event to delete:  359
Event to delete:  363
Event to delete:  385
Event to delete:  394
Event to delete:  396
Event to delete:  397
Event to delete:  403
Event to delete:  425
Event to delete:  463
Event to delete:  470
Event to delete:  478
Event to delete:  484
Event to delete:  492
Event to delete:  501
Event to delete:  506
Event to delete:  509
Event to delete:  51

In [ ]:
np.save("cuttedImages.npy", cuttedImages)

In [ ]:
cuttedImages.shape

(927, 189498)